In [1]:
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from scipy.interpolate import interp1d

In [2]:
from pathlib import Path

import pandas as pd

DATA_ROOT = Path('..') / 'data'

dfs = []
activity_labels = ['bed', 'chair', 'lying', 'ambulating']
default_names = ['time', 'front', 'vertical', 'lateral', 'sensor_id', 'rssi', 'phase', 'frequency', 'activity']
for data_file in Path(DATA_ROOT).rglob('d[12]p??[FM]'):
    df = pd.read_csv(data_file, names=default_names)
    df['activity_label'] = df['activity'].apply(lambda i: activity_labels[i - 1])
    df['gender_label'] = str(data_file)[-1]
    df['participant'] = data_file.name
    
    # Add a column indicating order of the activities for a particiapnt.
    df = df.sort_values(by=['time'])
    df['activity_sequence'] = (df['activity'].shift(1) != df['activity']).cumsum()
    dfs.append(df)

sensor_df = pd.concat(dfs, axis='index')
sensor_df = sensor_df.sort_values(by=['participant', 'time'])

sensor_df.head()

time    front  vertical   lateral  sensor_id  rssi   phase  frequency  \
0  0.00  0.27203   1.00820 -0.082102          1 -63.5  2.4252     924.25   
1  0.50  0.27203   1.00820 -0.082102          1 -63.0  4.7369     921.75   
2  1.50  0.44791   0.91636 -0.013684          1 -63.5  3.0311     923.75   
3  1.75  0.44791   0.91636 -0.013684          1 -63.0  2.0371     921.25   
4  2.50  0.34238   0.96229 -0.059296          1 -63.5  5.8920     920.25   

   activity activity_label gender_label participant  activity_sequence  
0         1            bed            M      d1p01M                  1  
1         1            bed            M      d1p01M                  1  
2         1            bed            M      d1p01M                  1  
3         1            bed            M      d1p01M                  1  
4         1            bed            M      d1p01M                  1

In [3]:
def normalize_time_values(df):
    return pd.DataFrame(dict(t_norm=np.linspace(0, 100, len(df))))

sensor_df['t_norm'] = (sensor_df.groupby(['participant', 'activity_sequence'])
                       .apply(normalize_time_values)
                       .reset_index(drop=True)['t_norm'])
sensor_df.head()

time    front  vertical   lateral  sensor_id  rssi   phase  frequency  \
0  0.00  0.27203   1.00820 -0.082102          1 -63.5  2.4252     924.25   
1  0.50  0.27203   1.00820 -0.082102          1 -63.0  4.7369     921.75   
2  1.50  0.44791   0.91636 -0.013684          1 -63.5  3.0311     923.75   
3  1.75  0.44791   0.91636 -0.013684          1 -63.0  2.0371     921.25   
4  2.50  0.34238   0.96229 -0.059296          1 -63.5  5.8920     920.25   

   activity activity_label gender_label participant  activity_sequence  \
0         1            bed            M      d1p01M                  1   
1         1            bed            M      d1p01M                  1   
2         1            bed            M      d1p01M                  1   
3         1            bed            M      d1p01M                  1   
4         1            bed            M      d1p01M                  1   

     t_norm  
0  0.000000  
1  1.851852  
2  3.703704  
3  5.555556  
4  7.407407

In [4]:
def interpolate(v, t_norm):
    t = np.linspace(min(t_norm), max(t_norm), len(v))
    if len(v) == 1:
        v = [v[0]] * 2
        t = [min(t_norm), max(t_norm)]
    try:
        std = np.std(v)
        mn = np.mean(v)
        z_score = (v - mn) / std if std else v - mn
        f = interp1d(t, v)
    except ValueError:
        raise
    v_norm = f(t_norm)
    return v_norm

def interpolate_sensor_data(df):
    data = {}
    n = 40
    for column in ['participant', 'activity', 'activity_label', 'activity_sequence']:
        data[column] = [df.iloc[0][column]] * n
    t_norm = np.linspace(0, 100, n)
    data['t_norm'] = t_norm
    for column in ['front', 'lateral', 'vertical']:
        data[column] = interpolate(df[column].values, t_norm)
    return pd.DataFrame(data)
    

In [5]:
norm_df = (sensor_df.groupby(['participant', 'activity_sequence'])
           .apply(interpolate_sensor_data)
           .reset_index(drop=True))

In [6]:
colors = px.colors.qualitative.D3
values = ['front', 'lateral', 'vertical']
SENSOR_COLORS = {
    value: colors[i] for i, value in enumerate(values)}

In [16]:
np.random.normal(size=30)

array([ 0.33250129,  0.98424076,  1.30716998, -0.69166108,  0.25925683,
       -1.60887814,  0.63289648,  0.96194281,  0.50188834, -2.26056013,
        0.30565972, -0.62957013,  0.80914292,  0.8463888 ,  0.98052953,
        0.5850161 ,  1.24207598, -0.34127969,  1.52714691,  0.67519322,
       -0.86577337, -1.59470713,  0.36204521,  1.17452981,  2.33849367,
        0.88269532,  0.82572724,  0.80623107, -1.46248437, -0.78050477])

In [17]:
activity_labels = sorted(norm_df['activity_label'].unique())

fig = make_subplots(
    rows=2, 
    cols=2, 
    vertical_spacing=0.1,
    horizontal_spacing=0.1,
    subplot_titles=activity_labels)

first = True
mode = 'lines+markers'
for _, activity_df in norm_df.groupby(['participant', 'activity_sequence']):
    activity_label = activity_df['activity_label'].values[0]
    i = activity_labels.index(activity_label)
    
    row = i // 2 + 1
    col = i % 2 + 1
    for sensor in ['front', 'lateral', 'vertical']:
        fig.add_trace(
            go.Scattergl(
                x=activity_df['t_norm'] + np.random.normal(size=len(activity_df)), 
                y=activity_df[sensor],
                marker_color=SENSOR_COLORS[sensor],
                opacity=0.0625,
                name=sensor,
                showlegend=False,
                legendgroup=sensor,
                mode=mode), row=row, col=col)
    first = False

# Just for legend :p
for sensor in ['front', 'lateral', 'vertical']:
    fig.add_trace(
        go.Scattergl(
            x=[0], 
            y=[0],
            marker_color=SENSOR_COLORS[sensor],
            name=sensor,
            showlegend=True,
            legendgroup=sensor,
            mode=mode))
    
fig.update_yaxes(range=[-2,2], showgrid=False, zeroline=True, showticklabels=False)
fig.update_xaxes(showgrid=False, showticklabels=False, zeroline=True)
fig.update_layout(width=800, height=600, margin=dict(l=16, r=16, t=64, b=16))
fig.show()
